# Exercise session 1: Overview of the Xpress Python Interface

## Creating a simple LP

First, create the simple linear program:

$$
\begin{array}{lll}
  \min & x + y\\
  \textrm{s.t.} & 2x + 3y \ge 6\\
                & 4x + 2y \ge 7\\
                & x,y \ge 0
\end{array}
$$

In [ ]:
# Location of manual and examples can be found by calling appropriate functions:

import xpress
print(xpress.manual())
print(xpress.examples())

In [ ]:
import xpress as xp

x = xp.var(name='myvar_1') # variables by default non-negative
y = xp.var(name='myvar_2')

constr1 = 2*x + 3*y >= 6
constr2 = 4*x + 2*y >= 7

obj = x + y

p = xp.problem(x, y,              # <-- variables (always first to be added)
               constr1, constr2,  # <-- then constraints and objective (in no order)
               obj)

# Uncomment the following if you want to turn off logging from Xpress
# p.controls.outputlog = 0

p.solve()

print(f'solution: x={p.getSolution(x)}, y={p.getSolution(y)}')

# Same effect with this call that uses names instead of objects:
# print(f'solution: x={p.getSolution('myvar_1')}, y={p.getSolution('myvar_2')}')

Add the constraint $x + 2y \le 2$ to the problem, then re-solve. The problem should now be infeasible.

In [ ]:
# STUDENT EXERCISE

bad_constr = x + 2*y <= 2
p.addConstraint(bad_constr)
p.solve()

Use the `iisall` function to understand what made the problem infeasible. If needed, type `help(p.iisall)` for its docstring.

In [ ]:
p.iisall()

Now delete the constraint (using the `problem.delConstraint` method) and, just to avoid the same solve as before, change the objective function coefficient of $x$ to 4. Then re-solve and print primal and dual solution using `problem.getSolution` for the primal solution and `problem.getDual` for the dual solution. Recall that these functions can be called without arguments to obtain the whole vector, or with a variable/constraint object to get one or more values.

In [ ]:
p.delConstraint(bad_constr)
p.chgobj([x],[4])
p.solve()

print(f'Solution: x={p.getSolution(x)}, y={p.getSolution(y)}')
print(f'Dual: constr1->{p.getDual(constr1)}, constr2->{p.getDual(constr2)}')

## Knapsack problem

Formulate and solve a knapsack problem with the following value/weight vectors:

$$
\begin{array}{lllrrrrrrr}
v& =& (12,&15,& 9,&11,& 8,& 7,&5)\\
w& =& (13, &18,& 9,& 12,& 8,& 10,& 4)
\end{array}
$$

and with knapsack capacity $C=40$. You will need the `xpress.Sum` operator. The formulation of a knapsack problem is as follows:

$$
\begin{array}{lllrrrrrrr}
\max & \sum_{i=1}^n v_i x_i\\
\textrm{s.t.} & \sum_{i=1}^n w_i x_i \le C\\
& x_i \in \{0,1\} \forall i=1,\ldots{},n
\end{array}
$$



In [ ]:
import xpress as xp

v = [12,15,9,11,8, 7,5]
w = [13,18,9,12,8,10,4]
C = 40

n = len(v)
x = [xp.var(vartype=xp.binary) for _ in range(n)]

k_con = xp.Sum(w[i]*x[i] for i in range(n)) <= C
k_obj = xp.Sum(v[i]*x[i] for i in range(n))

p = xp.problem(x, k_con, k_obj, sense=xp.maximize)  # optimization sense is min by default

p.solve()

print(p.getSolution())

## Reading and solving a MIP

Let's try to solve something bigger, like a file from the MIPLIB 2017 collection. Specifically, `roi2alpha3n4`. It should be available in the directory with this exercise session; load it and solve it as a Python problem.

In [ ]:
filename = 'mipinst.mps.gz'
p = xp.problem()
p.read(filename)
p.controls.maxtime = -30
p.solve()

Add a new constraint: the norm of the variable vector is at most 10. Even if the problem was read from a file, you can get the vector of all variables with `problem.getVariable`.

Note that before the constraint is added we'll have to postsolve the problem (using the `problem.postsolve()` function) as, for reasons of performance, the problem remains in a presolved state after the `solve()` call.

In [ ]:
import numpy as np
p.postsolve()
v = np.array(p.getVariable(), dtype=xp.npvar)

p.addConstraint(xp.Dot(v,v) <= 100)

# Or equivalently:
#
# v = p.getVariable()
# p.addConstraint(xp.Sum(i**2 for i in v) <= 100)
#
# Note that this form does not require importing numpy

p.controls.maxtime=-30
p.solve()

With a real MIP at hand, how about we try to see the structure of the coefficient structure from a graphical standpoint? Use `matplotlib` to draw a density chart.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import scipy.sparse as sparse

p.postsolve()
mstart, mclind, dmatval = [], [], []
p.getrows(mstart, mclind, dmatval, p.attributes.elems, 0, p.attributes.rows - 1)

# Suppose the matrix is as follows:
#
# A = [0 0 2 9 0 7
#      1 0 0 5 1 9
#      0 0 8 5 0 3]
#
# Then we want a sparse representation where we store only information
# on the nonzero coefficients. This comes with three lists (I'm using
# spaces liberally to show information of each row):
#
# coeff   = [2 9 7   1 5 1 9   8 5 3]   <-- all nonzeros in the order they appear (first row, then column)
# indices = [2 3 5   0 3 4 5   2 3 5]
# mstart  = [0 3 7 10]
#
# Here, mstart contains an entry for each row i: the position, within coeff and indices,
# of the first element of row i. This is obviously 0 for the first row. The difference
# between two consecutive elements of mstart is the number of corresponding nonzeros in a row.
# There are m+1 elements in mstart if the problem has m rows. The (m+1)-st contains the 
# total number of elements in the problem.

# mclind contains variable objects, not indices.
# Extract the index for all of them with getIndex()
mclindnum = [p.getIndex(v) for v in mclind]
A = sparse.csr_matrix ((dmatval, mclindnum, mstart))

# plt.matshow(A.toarray())
plt.spy(A, markersize=.2)
plt.show()

### NumPy operators and arrays of variables/constraints

NumPy is an essential toolbox for Python users. The Xpress Python interface can handle (multi-)arrays of floats, variables, expressions, constraints as naturally as with lists thereof.

In [ ]:
import numpy as np

# The following two statements create two equivalent NumPy arrays of variables.
x = np.array([xp.var(vartype=xp.binary, name='x({})'.format(i)) for i in range(20)], dtype=xp.npvar)
y = xp.vars(20,      vartype=xp.binary, name='x')


We can also rewrite the knapsack problem using NumPy constructs.

In [ ]:
import xpress as xp
import numpy as np

v = np.array([12,15,9,11,8, 7,5])
w = np.array([13,18,9,12,8,10,4])
C = 40

n = len(v)
x = xp.vars(n, vartype=xp.binary)

# xp.Dot only works with numpy arrays (of numbers and/or Xpress objects: expressions and variables)
k_con = xp.Dot(w,x) <= C
k_obj = xp.Dot(v,x)

p = xp.problem(x, k_con, k_obj, sense=xp.maximize)

p.solve()

print(p.getSolution())

Exercise: Create a random 20x30 numpy matrix $A$ and vectors ${\bf b}$ and ${\bf c}$, then create a problem with c as objective function coefficient vector and constraints $A{\bf x} \le {\bf b}$.

In [ ]:
n = 30 # number of variables
m = 20 # number of constraints

A = np.random.random((m,n))
b = np.random.random(m)
c = np.random.random(n)

x = xp.vars(n)

objective = xp.Dot(c, x)
consys = xp.Dot(A, x) <= b

p = xp.problem(x, objective, consys, sense=xp.maximize)

p.solve()

Let's spice it up: make the objective function quadratic, with a matrix $Q$ that is PSD but not necessarily diagonal. Make the objective

$$
(x-x_0)^T Q (x-x_0)
$$

In [ ]:
# The following has a strong-enough diagonal that we're sure it is PSD (in fact, it's diagonally dominant)
Q = np.random.random((n,n)) - .5 + 3*n*np.eye(n)

x0 = 10 * np.random.random(n)  # Creates a point with random coordinates in [0,10]

# Minimize weighted (with Q) distance between x and x0: (x-x0)' Q (x-x0)

obj2 = xp.Dot((x-x0), Q, (x-x0))

p.setObjective(obj2, sense=xp.minimize)
p.solve()

Obviously we can use arrays of variables in constraints. Let's consider the following problem:

### Production planning with quadratic cost

A factory must plan production on one machine for the upcoming $N=12$ days. If, on one day, the machine is on, it must pay a fixed cost F, regardless of how much is produced on that machine. If the machine is on, the production must range between L and U. It must also pay a cost that is C times the square of the produced amount.

The demand at a given day is $w_i$, and the unsold product can be stored in a storage container of capacity $M$. Finally, the storage level at the end of the $N$ days must be the same as the beginning, which is set as $S$.

**Model**. Define two classes of variables, $x$ (continuous) and $y$ (binary), indicating the amount of production in a given day and whether the machine is on or off, respectively. Also, introduce a storage variable $s$ that is also indexed by the set of periods.

In [ ]:
import xpress as xp

n = 12  # number of periods
N = range(n)

# Input parameters

C = 2   # proportional cost
F = 9000  # fixed cost
L = 10   # min. production level
U = 90   # max. production level
M = 170  # maximum storage level
S = 25   # initial storage level

# Demand
w = [60, 15, 25, 70, 70, 85, 10, 5, 65, 40, 50, 15]

# Variables

x = [xp.var() for _ in N]
y = [xp.var(vartype=xp.binary) for _ in N]
s = [xp.var(ub=M) for _ in range(n + 1)]  # Can assign upper bound of M immediately

# Total production cost (to be minimized)
objective = xp.Sum(F*y[i] + C*y[i]*x[i]**2 for i in N)

# y determines bounds on x

x_lb = [x[i] >= L*y[i] for i in N]
x_ub = [x[i] <= U*y[i] for i in N]

# storage at last period

store_end = s[n] == S
store_ini = s[0] == S

# Production balance

balance = [s[i] + x[i] == s[i+1] + w[i] for i in N]  # Conservation at each time period

p = xp.problem(x, y, s,
               objective,
               x_lb, x_ub, store_end, store_ini, balance)

p.solve()

print('time demand machine productn storage')
for i in N:
    print('{0:4d} {1:6d} {2:7.0f} {3:8.4f} {4:7.4f}'.format(i, w[i],
                                                            p.getSolution(y[i]),
                                                            p.getSolution(x[i]),
                                                            p.getSolution(s[i])))

**Homework**: Rewrite the problem using NumPy for defining parameters, variables, constraints, and objective.

In [ ]:
# STUDENT EXERCISE

import xpress as xp
import numpy as np

# Demand
w = np.array(w)

# Variables

x = xp.vars(n, name='prod')
y = xp.vars(n, vartype=xp.binary, name='machine')
s = xp.vars(n + 1, ub=M, name='storage')  # Can assign upper bound of M immediately

# Total production cost (to be minimized)
objective = xp.Sum(F*y + C*x**2)

# y determines bounds on x

x_lb = x >= L*y
x_ub = x <= U*y

# storage at last period

store_end = s[n] == S
store_ini = s[0] == S

# Production balance

balance = s[:n] + x == s[1:] + w # Conservation at each time period

p = xp.problem(x, y, s,
               objective,
               x_lb, x_ub, store_end, store_ini, balance)

p.solve()

print('time demand machine productn storage')
for i in N:
    print('{0:4d} {1:6d} {2:7.0f} {3:8.4f} {4:7.4f}'.format(i, w[i],
                                                            p.getSolution(y[i]),
                                                            p.getSolution(x[i]),
                                                            p.getSolution(s[i])))